In [72]:
import duckdb
import pandas as pd
import folium

In [7]:
con = duckdb.connect("../data/healthkit-sqlite-2023-11-17.db")

In [8]:
con.install_extension("sqlite")

In [9]:
con.load_extension("sqlite")

In [10]:
con.sql("PRAGMA show_tables")

┌─────────────────────────────────┐
│              name               │
│             varchar             │
├─────────────────────────────────┤
│ activity_summary                │
│ rActiveEnergyBurned             │
│ rAppleExerciseTime              │
│ rAppleStandHour                 │
│ rAppleStandTime                 │
│ rAppleWalkingSteadiness         │
│ rAudioExposureEvent             │
│ rBasalEnergyBurned              │
│ rBloodPressureDiastolic         │
│ rBloodPressureSystolic          │
│          ·                      │
│          ·                      │
│          ·                      │
│ rSwimmingStrokeCount            │
│ rTimeInDaylight                 │
│ rVO2Max                         │
│ rWalkingAsymmetryPercentage     │
│ rWalkingDoubleSupportPercentage │
│ rWalkingHeartRateAverage        │
│ rWalkingSpeed                   │
│ rWalkingStepLength              │
│ workout_points                  │
│ workouts                        │
├───────────────────────────

In [63]:
camino_sql = "SELECT * from workouts WHERE sourceName != 'AllTrails' AND startDate >= '2023-10-10' AND startDate <= '2023-10-17' AND duration > 100"

In [64]:
workouts_df = con.sql(camino_sql).to_df()

In [65]:
workouts_df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 9 entries, 0 to 8
Data columns (total 44 columns):
 #   Column                                  Non-Null Count  Dtype 
---  ------                                  --------------  ----- 
 0   id                                      9 non-null      object
 1   workoutActivityType                     9 non-null      object
 2   duration                                9 non-null      object
 3   durationUnit                            9 non-null      object
 4   sourceName                              9 non-null      object
 5   sourceVersion                           9 non-null      object
 6   creationDate                            9 non-null      object
 7   startDate                               9 non-null      object
 8   endDate                                 9 non-null      object
 9   metadata_HKGroupFitness                 0 non-null      object
 10  metadata_HKWorkoutBrandName             0 non-null      object
 11  metadata_H

In [66]:
workouts_df.columns

Index(['id', 'workoutActivityType', 'duration', 'durationUnit', 'sourceName',
       'sourceVersion', 'creationDate', 'startDate', 'endDate',
       'metadata_HKGroupFitness', 'metadata_HKWorkoutBrandName',
       'metadata_HKTimeZone', 'metadata_HKCoachedWorkout',
       'metadata_HKWasUserEntered', 'workout_events',
       'metadata_HKWeatherTemperature', 'metadata_HKWeatherHumidity', 'device',
       'metadata_HKIndoorWorkout', 'metadata_HKElevationAscended',
       'metadata_HKSwimmingLocationType', 'metadata_HKAverageMETs',
       'metadata_HEALTHFIT_SUB_SPORT', 'metadata_HEALTHFIT_ROUTE',
       'metadata_HEALTHFIT_FILE_TYPE', 'metadata_HKMaximumSpeed',
       'metadata_HEALTHFIT_TOTAL_MOVING_TIME',
       'metadata_HEALTHFIT_TOTAL_DISTANCE',
       'metadata_HEALTHFIT_MAX_RUNNING_CADENCE',
       'metadata_HEALTHFIT_MIN_ALTITUDE',
       'metadata_HEALTHFIT_AVG_RUNNING_CADENCE',
       'metadata_HEALTHFIT_APP_BUILD', 'metadata_HEALTHFIT_FIT_SPORT',
       'metadata_HEALTHFIT_FIT

In [67]:
drop_cols = [
    "workoutActivityType",
    "durationUnit",
    "sourceVersion",
    "metadata_HKGroupFitness",
    "metadata_HKWorkoutBrandName",
    "metadata_HKTimeZone",
    "metadata_HKCoachedWorkout",
    "metadata_HKWasUserEntered",
    "workout_events",
    "metadata_HKWeatherTemperature",
    "metadata_HKWeatherHumidity",
    "metadata_HKIndoorWorkout",
    "metadata_HKElevationAscended",
    "metadata_HKSwimmingLocationType",
    "metadata_HKAverageMETs",
    "metadata_HEALTHFIT_SUB_SPORT",
    "metadata_HEALTHFIT_ROUTE",
    "metadata_HEALTHFIT_FILE_TYPE",
    "metadata_HKMaximumSpeed",
    "metadata_HEALTHFIT_TOTAL_MOVING_TIME",
    "metadata_HEALTHFIT_TOTAL_DISTANCE",
    "metadata_HEALTHFIT_MAX_RUNNING_CADENCE",
    "metadata_HEALTHFIT_MIN_ALTITUDE",
    "metadata_HEALTHFIT_AVG_RUNNING_CADENCE",
    "metadata_HEALTHFIT_APP_BUILD",
    "metadata_HEALTHFIT_FIT_SPORT",
    "metadata_HEALTHFIT_FIT_SUB_SPORT",
    "metadata_HEALTHFIT_MAX_ALTITUDE",
    "metadata_HEALTHFIT_FIT_MANUFACTURER",
    "metadata_HEALTHFIT_TOTAL_STRIDES",
    "metadata_HEALTHFIT_FIT_SERIAL_NUMBER",
    "metadata_HEALTHFIT_SPORT",
    "metadata_HKAverageSpeed",
    "metadata_HEALTHFIT_APP_VERSION",
    "metadata_HKExternalUUID",
    "metadata_HKElevationDescended",
    "metadata_HKLapLength",
]

In [68]:
workouts_df.drop(labels=drop_cols, axis=1, inplace=True)

In [69]:
workouts_df

id           duration durationUnit  \
0  a27ca17d23f5e4dc91a20baaf1899325fed1d65b   111.755210117499          min   
1  9ad85b689eb5aa334b10e5e275221ccfe544ee18  295.3440696001053          min   
2  762460bb730747270c0b3fd6dc9513ee683e2e61  159.4728589514891          min   
3  85b8287214792712d9d3f2e9e9e813899b5b7ecc  272.1293779174487          min   
4  33c4c42faf1670bfbb0cd07b37003446f004b40b  331.8347500840823          min   
5  5f7f1cf5a978ad3aa0293f4d6911d6be350bd65f  395.3480985005697          min   
6  25499763e5d058577ece4c6e2e51f8ea028eb3cf  395.1284047663212          min   
7  5dc141afe96c0342433e188ae3da09ef114350ff  348.3012007991473          min   
8  1acfd59e813d94820ae980cdd345386e5ec39a17  130.5475179314613          min   

                          sourceName sourceVersion               creationDate  \
0  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-10 06:28:04 +1100   
1  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-10 22:27:02 +1100   
2  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-11 03:06:15 +1100   
3  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-12 03:38:41 +1100   
4  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-13 01:00:30 +1100   
5  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-13 23:41:42 +1100   
6  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-15 01:28:53 +1100   
7  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-16 03:41:48 +1100   
8  Michael and Ai Leen’s Apple Watch        10.0.1  2023-10-16 21:49:34 +1100   

                   startDate                    endDate  \
0  2023-10-10 04:36:12 +1100  2023-10-10 06:27:57 +1100   
1  2023-10-10 17:31:21 +1100  2023-10-10 22:26:42 +1100   
2  2023-10-10 23:59:30 +1100  2023-10-11 03:05:53 +1100   
3  2023-10-11 19:24:03 +1100  2023-10-12 03:38:15 +1100   
4  2023-10-12 19:28:15 +1100  2023-10-13 01:00:05 +1100   
5  2023-10-13 17:05:33 +1100  2023-10-13 23:40:54 +1100   
6  2023-10-14 18:51:52 +1100  2023-10-15 01:27:00 +1100   
7  2023-10-15 18:07:01 +1100  2023-10-16 03:37:24 +1100   
8  2023-10-16 19:38:40 +1100  2023-10-16 21:49:13 +1100   

                                              device  
0  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
1  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
2  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
3  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
4  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
5  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
6  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
7  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...  
8  <<HKDevice: 0x2821bb570>, name:Apple Watch, ma...

In [82]:
walk_id = con.sql(camino_sql.replace("*", "id")).to_df()

In [93]:
walk_id["id"].values.tolist()

['a27ca17d23f5e4dc91a20baaf1899325fed1d65b',
 '9ad85b689eb5aa334b10e5e275221ccfe544ee18',
 '762460bb730747270c0b3fd6dc9513ee683e2e61',
 '85b8287214792712d9d3f2e9e9e813899b5b7ecc',
 '33c4c42faf1670bfbb0cd07b37003446f004b40b',
 '5f7f1cf5a978ad3aa0293f4d6911d6be350bd65f',
 '25499763e5d058577ece4c6e2e51f8ea028eb3cf',
 '5dc141afe96c0342433e188ae3da09ef114350ff',
 '1acfd59e813d94820ae980cdd345386e5ec39a17']

In [84]:
walk_sql = "SELECT * FROM workout_points WHERE workout_id = 'WORKOUT_ID'"

In [85]:
walk_df = con.sql(walk_sql.replace("WORKOUT_ID", walk_id["id"].iloc[1])).to_df()

In [102]:
m = folium.Map(location=[43.3183, -1.9812], zoom_start=12, tiles="openstreetmap")

In [103]:
def create_map(m, df):
    points = df[["latitude", "longitude"]].values.tolist()
    folium.PolyLine(points, color="blue", weight=3.5, opacity=1).add_to(m)
    folium.Marker([df["latitude"].iloc[0], df["longitude"].iloc[0]]).add_to(m)
    return m

In [106]:
for id in walk_id["id"].values.tolist()[1:]:
    walk_df = con.sql(walk_sql.replace("WORKOUT_ID", id)).to_df()
    m = create_map(m, walk_df)

In [107]:
m